## LabJack Thermocouple to CSV Reader

Author: [JohnPaul Mitiguy](https://profiles.stanford.edu/intranet/johnpaul-mitiguy)

Date of Script Creation: Summer 2024
__________

### TLDR

1. [Install LJM library](#1-install-ljm-library)
2. [Connect LabJack w/thermocouple(s) to USB port](#2-connect-labjack-wthermocouples-to-usb-port)
3. [Create 2 empty CSV files & enter filepaths into Python Script](#3-create-2-empty-csv-files--enter-filepaths-into-python-script)
4. [Manipulate variables accordingly](#4-manipulate-variables-accordingly)
5. [Run Python Script](#5-run-python-script)
6. [Boot Node-RED from Command Prompt](#6-boot-node-red-from-command-prompt)
7. [Open Node-RED Dashboard](#7-open-node-red-dashboard)

____________

### Instructions

See <https://github.com/labjack/labjack-ljm-python> for more examples using the LJM library with Python.

Many installations will require admin privileges.

________

#### 1. Install LJM Library

See <https://support.labjack.com/docs/ljm-software-installer-downloads-t4-t7-t8-digit> for installation instructions for the LJM library (to read data from LabJack). This will be a .exe installation - not a pip installation. The LJM library (used by Kipling, etc.) is the only library I am aware of that can read LabJack data over a USB (as opposed to WiFi or Ethernet). See <https://support.labjack.com/docs/3-1-modbus-map-t-series-datasheet> for programming information that can be used to calculate temperature.

#### 2. Connect LabJack w/thermocouple(s) to USB port

See <https://support.labjack.com/docs/using-a-thermocouple-with-the-t7> for a helpful guide on how to use the LabJack with thermocouples. Note: The instructions use Kipling software to read the data, which is replaced by this Python Script (and Node-RED). The ports used to connect the thermocouple(s) & the connecting board should be recorded for later use in the Python Script. When using a differential set-up, the positive end of the thermocouple should be connected to an even AIN port (e.g., AIN2). The negative end of the thermocouple should be connected to the positive AIN port + 1; for example, if the thermocouple's positive end is in AIN2, then its negative end should be in AIN3. Lastly, the resistor (e.g., 100K Ohm) should be connected from the same port as the thermocouple's negative end to ground.

#### 3. Create 2 empty CSV files & enter filepaths into Python Script

Create 2 empty files of CSV filetype (e.g., using Excel). One will be to recording temperature data, the other to record the temperature reading settings. In the temperature data CSV file, every row records temperature data at a different time instance. Each column records the temperature of a different sensor.

#### 4. Manipulate variables accordingly

In the block below, the user can/should manipulate the variables according to their needs & set-up.

**The filepaths should be changed to the correct filepaths of the CSVs**. The user should decided whether to delete the existing temperature data in the CSV file. Changing the variable to ``False` will append new temperature data after old ones.

The user can control the intervals at which to record temperature data. The LabJack can communicate to the LJM library over time intervals of a few milliseconds (<https://support.labjack.com/docs/a-1-data-rates-t-series-datasheet>), though I'm uncertain how fast Node-RED can read the data (possibly around every 0.5 s). The maximum time interval indicates the amount of time that the code should run for before ceasing execution.

The ``calcOffsetList`` determines which inputs to manually adjust to room temperature at the beginning of the code. This is used to ensure that all of the thermocouples start at the same temperature. Otherwise, the thermocouples will read temperatures 2-3 deg C apart, even if they are reading the same real temperature. The user should input the room temperature that the thermocouples will adjust to. If the value is for a particular thermocouple, the thermocouple MUST start at room temperature for accurate readings.

The ``portList`` indicates which ports on the LabJack the positive end of the thermocouples are connected to. The ``cjcAddressList`` is used to adjust for the temperature of the board. ``60052`` should be used if the thermocouple is connected to the LabJack. ``60050`` should be used if the thermocouple is connected to the CB37 terminal board.

The ``diffConnectList`` indicates which port is being used as the negative end of the thermocouple for differential connections. For instance, if the positive end of the thermocouple is in the AIN4 port, and the negative end of the thermocouple is in the AIN5 port, then the integer ``5`` should be used in the corresponding index of this list. If a differential connection is not used, the integer ``199`` should be used instead.

The ``cjcOffsetList`` controls manual offset adjustments to temperature readings used to control variation between thermocouples & serves two functions. If the corresponding ``calcOffsetList`` boolean is ``True``, then the value initializes the offset value used in a later for/if statement. If the corresponding ``calcOffsetList`` boolean is ``False``, then this value will control how many degrees the output temperature reading is offset.

#### 5. Run Python Script

Run the Python Script. The script will output two sources of information. If ``calcOffsetList`` is ``True`` for a port, then the script will output the offset value for the temperature readings the first several times that readings are recorded. Once the script ceases to output offset values, the thermocouple can be transfered to a location with a different temperature without affecting the offset value. The other output of the script is the temperature readings of the connected thermocouples.

#### 6. Boot Node-RED from Command Prompt

Open Command Prompt on Windows. As long as Node-RED is installed on the computer, the user should be able to type ``node-red`` into the command prompt line and hit enter. I've found that this works in any directory. I've encountered problems when trying to accomplish this in Windows PowerShell on a SLAC-owned computer, as I encountered an error about running scripts. Instructions for installing Node-RED on a Windows machine can be found here: <https://nodered.org/docs/getting-started/windows>. After this, this user should open a browser window (e.g., Google Chrome) and enter ``http://localhost:1880/'' into the URL. Once Node-RED has been booted from the command prompt, this should open Node-RED correctly in a browser.

#### 7. Open Node-RED Dashboard

If node-red-dashboard is not already installed, follow the instructions here - <https://flows.nodered.org/node/node-red-dashboard> - to install the correct module to display the information in a dashboard window. The user also is required to have a deployed flow that handles the data from the CSV file. A working flow that accomplishes this can be found here - <https://slac-my.sharepoint.com/:u:/g/personal/jmitiguy_slac_stanford_edu/EU5c2WPN399Ot9o_n0UXZgIBiXk9nH8t3ON_nEb56VrBfg> - or [near the bottom of this file](#node-red-json-file-code) (needs to be saved as .json filetype - follow instructions [here](#node-red-json-file-code) to save as .json). Once the user has this json file, they can import it into Node-RED. After importing this file, there are 4 changes that the user will need to make concerning filepaths. These are in the 4 dark brown nodes labeled ``Watch for Updates``, ``Temperature Readings CSV File``, ``Watch for Updates``, and ``Settings CSV File``. The filepath for the first 2 nodes should match the filepath of the variable tempFilepath. The filepath for the second 2 nodes should match the filepath of the variable settingsFilepath (but with double back-slashes instead of single for Windows). After this updated flow has been deployed, the user can open their dashboard by clicking the more button (with 3 horizontal lines) next to the deploy button, then ``View``, then ``Dashboard``, then the pop-out icon located to the right of ``Theme``. The user should then be able to view the Node-RED dashboard with data.


#### Variables to be Manipulated by User

In [1]:
# CSV filepaths
tempFilepath = r"C:\Users\jmitiguy\OneDrive - SLAC National Accelerator Laboratory\1MP\Prototype\ExperimentalMeasurementData\TemperatureReadings.csv"
settingsFilepath = r"C:\Users\jmitiguy\OneDrive - SLAC National Accelerator Laboratory\1MP\Prototype\ExperimentalMeasurementData\TemperatureReadingSettings.csv"

# Delete existing info in CSV files
deleteCSVInfo = True

# Time
dataIntervalSec = 0.4 # s
maxTimeSec = 15 * 60 # s

# Determine whether to calculate offset
# Only mark "True" for thermocouples that have adjusted to room temperature before starting code
calcOffsetList = [True, True, True, True, True, True]
# calcOffsetList = [False, False, False, False, False, False]
# Room Temperature used to calculate offset values
roomTempC = 25.9 # deg C

# Thermocouple/LabJack Info
portList = ["AIN0", "AIN1", "AIN2", "AIN4", "AIN6", "AIN12"]
cjcAddressList = [60052, 60052, 60052, 60050, 60050, 60050]  # CJC Address - Temperature Dependent | 60052: TEMPERATURE_DEVICE_K (LabJack), 60050: TEMPERATURE_AIR_K (CB37 Terminal Board) # Units: K
diffConnectList = [199, 199, 3, 199, 199, 13] # Specifies the negative channel to be used for each positive channel. 199=Default=> Single-Ended. For base differential channels, positive must be an even channel from 0-12 and negative must be positive+1.
cjcOffsetList = [0, 0, 0, 0, 0, 0] # Offset to be applied to CJC reading. Default 0.0 # Units: K

#### Python Script only to be Modified by Programmer

In [2]:
# Import libraries
from labjack import ljm  
import sched
import time
import csv

# Create handle for T7
# handle = ljm.openS("T7", "USB", "470035665") # serial number
handle = ljm.openS("ANY", "ANY", "ANY") # serial number
handleInfo = ljm.getHandleInfo(handle)

# Delete file contents before inputting more data
if deleteCSVInfo:
    with open(tempFilepath, "w") as file:
        file.truncate() # deletes all data
    with open(settingsFilepath, "w") as file:
        file.truncate() # deletes all data



# newline='' ensures that newlines are handled consistently across platforms
with open(settingsFilepath, 'a', newline='') as file:
    writer = csv.writer(file)
    portsStringArr = [str(port) for port in portList] # [[str()]] need to pass it as one value (rather than 2, 4, ., 5, 3, 6, etc.)
    cjcAddressStringArr = [str(address) for address in cjcAddressList] # [[str()]] need to pass it as one value (rather than 2, 4, ., 5, 3, 6, etc.)
    diffConnectStringArr = [str(diffConnect) for diffConnect in diffConnectList] # [[str()]] need to pass it as one value (rather than 2, 4, ., 5, 3, 6, etc.)
    # writer.writerows(portsStringArr)
    writer.writerows([portsStringArr, cjcAddressStringArr, diffConnectStringArr])

tempResultList = [[]] # Initialize temperature result list
startTime = time.time() # compute start time
counter = 0 # Initialize counter

def compute_temp(scheduler, portList, cjcAddressList, calcOffsetList, counter):

    # Check if the elapsed time has exceeded the duration
    if (time.time() - startTime) > maxTimeSec:
        return  # Stop scheduling further calls
    
    counter += 1 # increment counter

    # schedule the next call first
    scheduler.enter(dataIntervalSec, 1, compute_temp, (scheduler, portList, cjcAddressList, calcOffsetList, counter))

    tempResultAllPorts = []

    for iPort in range(len(portList)):
        # https://support.labjack.com/docs/14-1-1-thermocouple-t7-t8-t-series-datasheet
        ljm.eWriteName(handle, (portList[iPort] + "_EF_INDEX"), 22) # Thermocouple type | 22 is type K thermocouple
        ljm.eWriteName(handle, (portList[iPort] + "_EF_CONFIG_A"), 1) # Temperature Units | 0: Kelvin, 1: Celsius, 2: Fahrenheit
        ljm.eWriteName(handle, (portList[iPort] + "_EF_CONFIG_B"), cjcAddressList[iPort]) # CJC Address - Temperature Dependent | 60052: TEMPERATURE_DEVICE_K (LabJack), 60050: TEMPERATURE_AIR_K (CB37 Terminal Board) # Units: K
        ljm.eWriteName(handle, (portList[iPort] + "_EF_CONFIG_D"), 1.0) # Slope to be applied to CJC reading. Default: 1.0 # Units: K/volt
        ljm.eWriteName(handle, (portList[iPort] + "_EF_CONFIG_E"), cjcOffsetList[iPort]) # Offset to be applied to CJC reading. Default 0.0 # Units: K 
        ljm.eWriteName(handle, (portList[iPort] + "_NEGATIVE_CH"), diffConnectList[iPort]) # Specifies the negative channel to be used for each positive channel. 199=Default=> Single-Ended. For base differential channels, positive must be an even channel from 0-12 and negative must be positive+1.
        tempResult = ljm.eReadName(handle, (portList[iPort] + "_EF_READ_A"))
        # voltageMeasured = ljm.eReadName(handle, (portList[iPort] + "_EF_READ_B"))
        # cjcTemp = ljm.eReadName(handle, (portList[iPort] + "_EF_READ_C"))
        # voltageCalc = ljm.eReadName(handle, (portList[iPort] + "_EF_READ_D"))

        # (First several times only) Calculate room temperature offset value for each thermocouple
        if calcOffsetList[iPort]:
            offsetCur = roomTempC - tempResult
            cjcOffsetList[iPort] += offsetCur/counter
            print("Offset value for " + portList[iPort] + " is: " + str(cjcOffsetList[iPort]) + " K")
            if counter >= 7:
                calcOffsetList[iPort] = False

        tempResultAllPorts.append(tempResult)

    # newline='' ensures that newlines are handled consistently across platforms
    with open(tempFilepath, 'a', newline='') as file:
        writer = csv.writer(file)
        tempResultStringArr = [[str(Num) for Num in tempResultAllPorts]] # [[str()]] need to pass it as one value (rather than 2, 4, ., 5, 3, 6, etc.)
        writer.writerows(tempResultStringArr)

    print(tempResultAllPorts)

    tempResultList.append(tempResultAllPorts)

# Consider using this method to avoid drift: https://stackoverflow.com/questions/474528/how-to-repeatedly-execute-a-function-every-x-seconds/25251804#25251804
s = sched.scheduler(time.time, time.sleep)
s.enter(dataIntervalSec, 1, compute_temp, (s, portList, cjcAddressList, calcOffsetList, counter))
s.run()




Offset value for AIN0 is: -0.4612670898437514 K
Offset value for AIN1 is: 1.3265747070312486 K
Offset value for AIN2 is: -0.2541137695312514 K
Offset value for AIN4 is: 1.1827148437499986 K
Offset value for AIN6 is: 1.2730163574218736 K
Offset value for AIN12 is: 2.6213134765624986 K
[26.36126708984375, 24.57342529296875, 26.15411376953125, 24.71728515625, 24.626983642578125, 23.2786865234375]
Offset value for AIN0 is: -0.46967163085937713 K
Offset value for AIN1 is: 1.3021331787109354 K
Offset value for AIN2 is: -0.27893676757812713 K
Offset value for AIN4 is: 1.1479888916015604 K
Offset value for AIN6 is: 1.2905364990234354 K
Offset value for AIN12 is: 2.599755859374998 K
[25.91680908203125, 25.948883056640625, 25.94964599609375, 25.969451904296875, 25.864959716796875, 25.943115234375]
Offset value for AIN0 is: -0.46595662434896096 K
Offset value for AIN1 is: 1.2940480550130182 K
Offset value for AIN2 is: -0.26115315755208596 K
Offset value for AIN4 is: 1.1453867594401015 K
Offset va

#### Node-RED JSON File Code

Save this code as a .json filetype. To do this in Visual Studio Code, go to ``File > New File``. When prompted to ``Select File Type or Enter File Name...``, type ``.json`` and hit ``Enter``. Then, paste the code below into the new .json file, and save it.

#### Old Script - Only for Reference

In [3]:
# """
# Demonstrates thermocouple configuration and  measurement using our LJTick-InAmp
# (commonly used with the T4)

# Relevant Documentation:

# Thermocouple App-Note:
#     https://labjack.com/support/app-notes/thermocouples

# LJM Library:
#     LJM Library Installer:
#         https:#labjack.com/support/software/installers/ljm
#     LJM Users Guide:
#         https:#labjack.com/support/software/api/ljm
#     Opening and Closing:
#         https:#labjack.com/support/software/api/ljm/function-reference/opening-and-closing
#     Single Value Functions(such as eReadName):
#         https:#labjack.com/support/software/api/ljm/function-reference/single-value-functions
#     TCVoltsToTemp:
#         https:#labjack.com/support/software/api/ud/function-reference/tcvoltstotemp

# T-Series and I/O:
#     Modbus Map:
#         https:#labjack.com/support/software/api/modbus/modbus-map
#     Analog Inputs:
#         https:#labjack.com/support/datasheets/t-series/ain
# """
# from labjack import ljm
# import sys

# if __name__ == "__main__":
#     # Open first found LabJack
#     handle = ljm.openS("ANY", "ANY", "ANY")  # Any device, Any connection, Any identifier
#     #handle = ljm.openS("T7", "ANY", "ANY")  # T7 device, Any connection, Any identifier
#     #handle = ljm.openS("T4", "ANY", "ANY")  # T4 device, Any connection, Any identifier
#     #handle = ljm.open(ljm.constants.dtANY, ljm.constants.ctANY, "ANY")  # Any device, Any connection, Any identifier

#     info = ljm.getHandleInfo(handle)
#     print("Opened a LabJack with Device type: %i, Connection type: %i,\n"
#           "Serial number: %i, IP address: %s, Port: %i,\nMax bytes per MB: %i" %
#           (info[0], info[1], info[2], ljm.numberToIP(info[3]), info[4], info[5]))
#     deviceType = info[0]

#     # Read 10 times
#     numIterations = 10
#     # Take a measurement of a thermocouple connected to AIN0
#     # That would be INA of an InAmp connected to the VS/GND/AIN0/AIN1 terminals
#     channelName = "AIN0"
#     # Gain setting on the InAmp
#     gain = 51
#     # Offset setting (V) on the InAmp
#     offset = 1.25
#     tcType = ljm.constants.ttK # Type K thermocouple
#     # thermocoupleType = ljm.constants.ttB # Type B thermocouple
#     # thermocoupleType = ljm.constants.ttE # Type E thermocouple
#     # thermocoupleType = ljm.constants.ttJ # Type J thermocouple
#     # thermocoupleType = ljm.constants.ttN # Type N thermocouple
#     # thermocoupleType = ljm.constants.ttR # Type R thermocouple
#     # thermocoupleType = ljm.constants.ttS # Type S thermocouple
#     # thermocoupleType = ljm.constants.ttT # Type T thermocouple
#     # thermocoupleType = ljm.constants.ttC # Type C thermocouple

#     # Set the resolution index to the default setting
#     # Default setting has different meanings depending on the device.
#     # See our AIN documentation (linked above) for more information
#     resIndexRegister = "%s_RESOLUTION_INDEX" % channelName
#     ljm.eWriteName(handle, resIndexRegister, 0)

#     # This section is for range and negative channel settings. The T4 does not
#     # support these configurations
#     if deviceType == ljm.constants.dtT7:
#         # ±10 V range setting
#         rangeRegister = "%s_RANGE" % channelName
#         ljm.eWriteName(handle, rangeRegister, 10)
#         # Set up a single ended measurement
#         negChannelValue = ljm.constants.GND
#         negChannelRegister = "%s_NEGATIVE_CH" % channelName
#         ljm.eWriteName(handle, negChannelRegister, negChannelValue)
#     elif deviceType == ljm.constants.dtT8:
#         print("\nThe T8 is not compatible with the InAmp, see our AIN_EF example")
#         exit(0)

#     print("\nReading thermocouple temperature %d times...\n" % numIterations)
#     i = 0
#     intervalHandle = 1
#     # Delay between readings (in microseconds)
#     ljm.startInterval(intervalHandle, 1000000)

#     while i < numIterations:
#         try:
#             # Read the InAmp output voltage and internal temp sensor at once
#             aNames = [channelName, "TEMPERATURE_DEVICE_K"]
#             [voltage, cjTempK] = ljm.eReadNames(handle, len(aNames), aNames)
#             # Convert the InAmp output to the raw thermocouple voltage
#             tcVolts = (voltage - offset) / gain
#             # Convert voltage to thermocouple temperature (K).
#             tcTempK = ljm.tcVoltsToTemp(tcType, tcVolts, cjTempK)
#             # Print the temperature read
#             print("%0.3f degrees Kelvin\n" % tcTempK)
#             i = i + 1
#             ljm.waitForNextInterval(intervalHandle)
#         except Exception:
#             print(sys.exc_info()[1])
#             break

#     # Close handles
#     ljm.cleanInterval(intervalHandle)
#     ljm.close(handle)
#     print("Done!")

In [4]:
# from labjack import ljm

# # Open first found LabJack
# handle = ljm.openS("T7","USB","ANY")
# # Call eReadName to read the serial number from the LabJack.
# name ="SERIAL_NUMBER"
# result = ljm.eReadName(handle, name)
# print("\neReadName result: ")
# print("    %s = %f"%(name, result))

# # Setup and call eReadAddress to read a value from the LabJack.
# address = 60028  # Serial number
# dataType = ljm.constants.UINT32
# result = ljm.eReadAddress(handle, address, dataType)

In [5]:
# from labjack import ljm


# # Open first found LabJack
# handle = ljm.openS("ANY", "ANY", "ANY")  # Any device, Any connection, Any identifier
# #handle = ljm.openS("T8", "ANY", "ANY")  # T8 device, Any connection, Any identifier
# #handle = ljm.openS("T7", "ANY", "ANY")  # T7 device, Any connection, Any identifier
# #handle = ljm.openS("T4", "ANY", "ANY")  # T4 device, Any connection, Any identifier
# #handle = ljm.open(ljm.constants.dtANY, ljm.constants.ctANY, "ANY")  # Any device, Any connection, Any identifier

# info = ljm.getHandleInfo(handle)
# print("Opened a LabJack with Device type: %i, Connection type: %i,\n"
#       "Serial number: %i, IP address: %s, Port: %i,\nMax bytes per MB: %i" %
#       (info[0], info[1], info[2], ljm.numberToIP(info[3]), info[4], info[5]))

# # Local constants to save screen space
# WRITE = ljm.constants.WRITE
# READ = ljm.constants.READ
# FLOAT32 = ljm.constants.FLOAT32
# UINT16 = ljm.constants.UINT16
# UINT32 = ljm.constants.UINT32

# # Setup and call eAddresses to write/read values to/from the LabJack.
# # Write 2.5V to DAC0,
# # write 12345 to TEST_UINT16,
# # read TEST_UINT16,
# # read serial number,
# # read product ID,
# # and read firmware version.
# numFrames = 6
# # [DAC0, TEST_UINT16, TEST_UINT16, SERIAL_NUMBER, PRODUCT_ID, FIRMWARE_VERSION]
# aAddresses = [1000, 55110, 55110, 60028, 60000, 60004]
# aDataTypes = [FLOAT32, UINT16, UINT16, UINT32, FLOAT32, FLOAT32]
# aWrites = [WRITE, WRITE, READ, READ, READ, READ]
# aNumValues = [1, 1, 1, 1, 1, 1]
# aValues = [2.5, 12345, 0, 0, 0, 0]
# results = ljm.eAddresses(handle, numFrames, aAddresses, aDataTypes, aWrites,
#                          aNumValues, aValues)

# print("\neAddresses results: ")
# start = 0
# for i in range(numFrames):
#     end = start + aNumValues[i]
#     print("    Address - %5i, data type - %i, write - %i, values: %s" %
#           (aAddresses[i], aDataTypes[i], aWrites[i], str(results[start:end])))
#     start = end

# # Close handle
# ljm.close(handle)

In [6]:
# from labjack import ljm

# handle = ljm.openS("T7", "USB", "ANY")

# # Read the voltage on AIN0
# voltage = ljm.eReadName(handle, "AIN0")

# print(voltage)
# voltageMV = voltage * 1000
# print(voltageMV)

In [7]:
# import numpy as np

# minTemp = -270 # deg C
# maxTemp = 109 # deg C
# interval = 1 # deg C

# tempList = np.arange(minTemp, (maxTemp + interval), interval)
# # https://www.pyromation.com/Downloads/Data/emfk_c.pdf
# thermocoupleRefListNegRawMV = [
# [-6.444, -6.446, -6.448, -6.450, -6.452, -6.453, -6.455, -6.456, -6.457, -6.458, ], # -6.441,
# [-6.408, -6.413, -6.417, -6.421, -6.425, -6.429, -6.432, -6.435, -6.438, -6.441, ], # -6.404,
# [-6.351, -6.358, -6.364, -6.370, -6.377, -6.382, -6.388, -6.393, -6.399, -6.404, ], # -6.344,
# [-6.271, -6.280, -6.289, -6.297, -6.306, -6.314, -6.322, -6.329, -6.337, -6.344, ], # -6.262,
# [-6.170, -6.181, -6.192, -6.202, -6.213, -6.223, -6.233, -6.243, -6.252, -6.262, ], # -6.158,
# [-6.048, -6.061, -6.074, -6.087, -6.099, -6.111, -6.123, -6.135, -6.147, -6.158, ], # -6.035,
# [-5.907, -5.922, -5.936, -5.951, -5.965, -5.980, -5.994, -6.007, -6.021, -6.035, ], # -5.891,
# [-5.747, -5.763, -5.780, -5.797, -5.813, -5.829, -5.845, -5.861, -5.876, -5.891, ], # -5.730,
# [-5.569, -5.588, -5.606, -5.624, -5.642, -5.660, -5.678, -5.695, -5.713, -5.730, ], # -5.550,
# [-5.374, -5.395, -5.415, -5.435, -5.454, -5.474, -5.493, -5.512, -5.531, -5.550, ], # -5.354,
# [-5.163, -5.185, -5.207, -5.228, -5.250, -5.271, -5.292, -5.313, -5.333, -5.354, ], # -5.141,
# [-4.936, -4.960, -4.983, -5.006, -5.029, -5.052, -5.074, -5.097, -5.119, -5.141, ], # -4.913,
# [-4.694, -4.719, -4.744, -4.768, -4.793, -4.817, -4.841, -4.865, -4.889, -4.913, ], # -4.669,
# [-4.437, -4.463, -4.490, -4.516, -4.542, -4.567, -4.593, -4.618, -4.644, -4.669, ], # -4.411,
# [-4.166, -4.194, -4.221, -4.249, -4.276, -4.303, -4.330, -4.357, -4.384, -4.411, ], # -4.138,
# [-3.882, -3.911, -3.939, -3.968, -3.997, -4.025, -4.054, -4.082, -4.110, -4.138, ], # -3.852,
# [-3.584, -3.614, -3.645, -3.675, -3.705, -3.734, -3.764, -3.794, -3.823, -3.852, ], # -3.554,
# [-3.274, -3.306, -3.337, -3.368, -3.400, -3.431, -3.462, -3.492, -3.523, -3.554, ], # -3.243,
# [-2.953, -2.986, -3.018, -3.050, -3.083, -3.115, -3.147, -3.179, -3.211, -3.243, ], # -2.920,
# [-2.620, -2.654, -2.688, -2.721, -2.755, -2.788, -2.821, -2.854, -2.887, -2.920, ], # -2.587,
# [-2.278, -2.312, -2.347, -2.382, -2.416, -2.450, -2.485, -2.519, -2.553, -2.587, ], # -2.243,
# [-1.925, -1.961, -1.996, -2.032, -2.067, -2.103, -2.138, -2.173, -2.208, -2.243, ], # -1.889,
# [-1.564, -1.600, -1.637, -1.673, -1.709, -1.745, -1.782, -1.818, -1.854, -1.889, ], # -1.527,
# [-1.194, -1.231, -1.268, -1.305, -1.343, -1.380, -1.417, -1.453, -1.490, -1.527, ], # -1.156,
# [-0.816, -0.854, -0.892, -0.930, -0.968, -1.006, -1.043, -1.081, -1.119, -1.156, ], # -0.778,
# [-0.431, -0.470, -0.508, -0.547, -0.586, -0.624, -0.663, -0.701, -0.739, -0.778, ], # -0.392,
# [-0.039, -0.079, -0.118, -0.157, -0.197, -0.236, -0.275, -0.314, -0.353, -0.392, ], #  0.000,
# ]
# thermocoupleRefListPosRawMV = [
# [ 0.000,  0.039,  0.079,  0.119,  0.158,  0.198,  0.238,  0.277,  0.317,  0.357, ], #  0.397,
# [ 0.397,  0.437,  0.477,  0.517,  0.557,  0.597,  0.637,  0.677,  0.718,  0.758, ], #  0.798,
# [ 0.798,  0.838,  0.879,  0.919,  0.960,  1.000,  1.041,  1.081,  1.122,  1.163, ], #  1.203,
# [ 1.203,  1.244,  1.285,  1.326,  1.366,  1.407,  1.448,  1.489,  1.530,  1.571, ], #  1.612,
# [ 1.612,  1.653,  1.694,  1.735,  1.776,  1.817,  1.858,  1.899,  1.941,  1.982, ], #  2.023,
# [ 2.023,  2.064,  2.106,  2.147,  2.188,  2.230,  2.271,  2.312,  2.354,  2.395, ], #  2.436,
# [ 2.436,  2.478,  2.519,  2.561,  2.602,  2.644,  2.685,  2.727,  2.768,  2.810, ], #  2.851,
# [ 2.851,  2.893,  2.934,  2.976,  3.017,  3.059,  3.100,  3.142,  3.184,  3.225, ], #  3.267,
# [ 3.267,  3.308,  3.350,  3.391,  3.433,  3.474,  3.516,  3.557,  3.599,  3.640, ], #  3.682,
# [ 3.682,  3.723,  3.765,  3.806,  3.848,  3.889,  3.931,  3.972,  4.013,  4.055, ], #  4.096,
# [ 4.096,  4.138,  4.179,  4.220,  4.262,  4.303,  4.344,  4.385,  4.427,  4.468, ], #  4.509,
# ]

# # thermocoupleRefListMV = np.zeros(len(thermocoupleRefListRaw) * len(thermocoupleRefListRaw[0]))
# thermocoupleRefListMV = []

# for iRow in range(len(thermocoupleRefListNegRawMV)):
#     for iCol in range(len(thermocoupleRefListNegRawMV[iRow])):
#         nextNum = thermocoupleRefListNegRawMV[iRow][(-1)*iCol - 1]
#         thermocoupleRefListMV.append(nextNum)

# for iRow in range(len(thermocoupleRefListPosRawMV)):
#     for iCol in range(len(thermocoupleRefListPosRawMV[iRow])):
#         nextNum = thermocoupleRefListPosRawMV[iRow][iCol]
#         thermocoupleRefListMV.append(nextNum)

# print(len(tempList))
# print(len(thermocoupleRefListMV))

# Num = 351
# print("mV: " + str(thermocoupleRefListMV[Num]) + " is " + str(tempList[Num]) + " deg C")

In [8]:
# for iV in range(len(thermocoupleRefListMV)):
#     # print(thermocoupleRefListMV[iV])
#     # print(voltageMV)
#     if thermocoupleRefListMV[iV] >= voltageMV:
#         temp = tempList[iV]
#         break

# print(temp)